In [3]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/digit-recognizer/sample_submission.csv
/kaggle/input/digit-recognizer/train.csv
/kaggle/input/digit-recognizer/test.csv


In [4]:
# import libs
import re
import plotly.express as px
import plotly.graph_objects as go
import pandas as pd
import numpy as np
import seaborn as sns
from zipfile import ZipFile
from PIL import Image
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
import cv2
from sklearn.model_selection import train_test_split
from sklearn.multiclass import OneVsOneClassifier
import tensorflow as tf
from sklearn.linear_model import Perceptron
from tensorflow import keras

2024-05-29 10:31:41.958152: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-05-29 10:31:41.958281: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-05-29 10:31:42.118261: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


# 1. Data Visualisation

In [5]:
# Data visualisation
train = pd.read_csv("/kaggle/input/digit-recognizer/train.csv")
test = pd.read_csv("/kaggle/input/digit-recognizer/test.csv")

In [6]:
train

label  pixel0  pixel1  pixel2  pixel3  pixel4  pixel5  pixel6  pixel7  \
0          1       0       0       0       0       0       0       0       0   
1          0       0       0       0       0       0       0       0       0   
2          1       0       0       0       0       0       0       0       0   
3          4       0       0       0       0       0       0       0       0   
4          0       0       0       0       0       0       0       0       0   
...      ...     ...     ...     ...     ...     ...     ...     ...     ...   
41995      0       0       0       0       0       0       0       0       0   
41996      1       0       0       0       0       0       0       0       0   
41997      7       0       0       0       0       0       0       0       0   
41998      6       0       0       0       0       0       0       0       0   
41999      9       0       0       0       0       0       0       0       0   

       pixel8  ...  pixel774  pixel775  pixel776  pixel777  pixel778  \
0           0  ...         0         0         0         0         0   
1           0  ...         0         0         0         0         0   
2           0  ...         0         0         0         0         0   
3           0  ...         0         0         0         0         0   
4           0  ...         0         0         0         0         0   
...       ...  ...       ...       ...       ...       ...       ...   
41995       0  ...         0         0         0         0         0   
41996       0  ...         0         0         0         0         0   
41997       0  ...         0         0         0         0         0   
41998       0  ...         0         0         0         0         0   
41999       0  ...         0         0         0         0         0   

       pixel779  pixel780  pixel781  pixel782  pixel783  
0             0         0         0         0         0  
1             0         0         0         0         0  
2             0         0         0         0         0  
3             0         0         0         0         0  
4             0         0         0         0         0  
...         ...       ...       ...       ...       ...  
41995         0         0         0         0         0  
41996         0         0         0         0         0  
41997         0         0         0         0         0  
41998         0         0         0         0         0  
41999         0         0         0         0         0  

[42000 rows x 785 columns]

In [7]:
X_train = train.loc[:, train.columns != 'label'].values
train_ar = np.empty((28,28,42_000))

for m in range(42_000): #digit
    for i in range(28): #rows
        for j in range(28): #columns
            train_ar[i][j][m] = X_train[m, i*28+j]

In [8]:
# train_ar is a three dimensional array of 28x28x42000. Let's display the digits one next to the other.
# We can put the 42000 digits in 200 columns and 210 rows. => arr of size (210x28, 200x28)
img_train_digits = np.empty((28, 5628))
col = np.empty((28, 28))
row_cnt = 0
px_cnt = 0
for m in range(42_000):
    px_cnt += 1
    col = np.hstack((col, train_ar[:, :, m]))
    if px_cnt % 200 == 0:
        if row_cnt == 0:
            img_train_digits = col
        else:
            img_train_digits = np.vstack((img_train_digits, col))
        row_cnt += 1
        col = np.empty((28, 28))
        
# Remove the first empty column
img_train_digits = img_train_digits[:, 29:]

In [9]:
img_train_digits.shape

(5880, 5599)

In [10]:
# Normalize the array values to fit in the range [0, 255]
img_train_digits = (img_train_digits - img_train_digits.min()) / (img_train_digits.max() - img_train_digits.min()) * 255
img_train_digits = img_train_digits.astype(np.uint8)

# Create the image using PIL
all_numbers_img = Image.fromarray(img_train_digits)

# Save the image to a temporary file
all_numbers_img.save('/kaggle/working/all_numbers_img.png')

In [11]:
# Display the saved image using matplotlib
img = mpimg.imread('/kaggle/working/all_numbers_img.png')
plt.figure(figsize=(20, 20))
plt.imshow(img, cmap='gray')
plt.axis('off')
plt.show()

# 1. Pairwise linear classifier
https://scikit-learn.org/stable/modules/generated/sklearn.multiclass.OneVsOneClassifier.html

In [12]:
train_df = pd.read_csv('/kaggle/input/digit-recognizer/train.csv')
test_df = pd.read_csv('/kaggle/input/digit-recognizer/test.csv')
X_train = train_df.loc[:, train_df.columns != 'label'].values
y_train = train_df['label'].values
X_test = test_df.values

In [13]:
X_train = train_df.loc[:, train_df.columns != 'label'].values[:35000]
y_train = train_df['label'].values[:35000]
X_test = train_df.loc[:, train_df.columns != 'label'].values[35000:]
y_test = train_df['label'].values[35000:]

In [14]:
clf = OneVsOneClassifier(
    Perceptron()).fit(X_train, y_train)#Perceptron(tol=1e-3, random_state=0)

In [15]:
clf.score(X_test,y_test)

0.9165714285714286

In [17]:
predictions = clf.predict(test_df.values)

# Prepare submission DataFrame
submission_df = pd.DataFrame({
    'ImageId': np.arange(1, len(predictions) + 1),
    'Label': predictions
})

# Save the submission file
submission_df.to_csv('/kaggle/working/results.csv', index=False)

# 2. Convolutional neural network

In [18]:
X_train = train_df.loc[:, train_df.columns != 'label'].values
all_ar = np.empty((42000,28,28,1))

for m in range(42000):#digit
    for i in range(28):#rows
        for j in range(28):#columns
            all_ar[m][i][j][0] = X_train[m,i*28+j]

In [19]:
x_train = all_ar[:30000,:,:,:]
y_train = train_df['label'].values[:30000]

x_val = all_ar[30000:35000,:,:,:]
y_val = train_df['label'].values[30000:35000]

x_test = all_ar[35000:42000,:,:,:]
y_test = train_df['label'].values[35000:42000]

In [20]:
def preprocess(x, y):
    x = tf.cast(x, tf.float32) / 255.0
    y = tf.cast(y, tf.int64)
    return x, y

def create_dataset(xs, ys, n_classes=10):
    
    ys = tf.one_hot(ys, depth=n_classes)
    return tf.data.Dataset.from_tensor_slices((xs, ys)) \
        .map(preprocess) \
        .shuffle(len(ys)) \
        .batch(200)

In [21]:
train_dataset = create_dataset(x_train, y_train)
val_dataset = create_dataset(x_val, y_val)
test_dataset = create_dataset(x_test, y_test)

In [22]:
model1 = keras.Sequential([
    keras.layers.Conv2D(100, (3, 3), activation='relu', kernel_initializer='he_uniform', input_shape=(28,28,1)),#input_shape is  (batch, rows, cols, channels) if data_format is "channels_last".
    
    keras.layers.MaxPooling2D((2, 2)),
    
    keras.layers.Conv2D(100, (3, 3), activation='relu', kernel_initializer='he_uniform'),#input_shape is  (batch, rows, cols, channels) if data_format is "channels_last".
    
    keras.layers.MaxPooling2D((2, 2)),
    
    keras.layers.Conv2D(100, (3, 3), activation='relu', kernel_initializer='he_uniform'),#input_shape is  (batch, rows, cols, channels) if data_format is "channels_last".
    
    keras.layers.Flatten(),
    
    keras.layers.Dense(
      units=100, activation='relu',  kernel_initializer='he_uniform'
    ),
    
    keras.layers.Dense(
      units=10, activation = 'softmax'
    )
])

#Conv2D(5, (3, 3), activation='relu', input_shape=(28,28))# filters, kernel_size 
#model.add(layers.MaxPooling2D((2, 2)))

##########################################################################################################################################################
model1.compile(
  optimizer=tf.keras.optimizers.SGD(learning_rate=0.005),
  loss=tf.losses.CategoricalCrossentropy(from_logits=True),
  metrics=['accuracy']
)

##########################################################################################################################################################
history = model1.fit(
    train_dataset.repeat(),
    epochs=50,
    steps_per_epoch=150,#train samples / batch size
    validation_data = val_dataset.repeat(),
    validation_steps=25#validation samples / batch size
)

Epoch 1/50


/opt/conda/lib/python3.10/site-packages/keras/src/layers/convolutional/base_conv.py:99: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(
/opt/conda/lib/python3.10/site-packages/keras/src/backend/tensorflow/nn.py:585: UserWarning: "`categorical_crossentropy` received `from_logits=True`, but the `output` argument was produced by a Softmax activation and thus does not represent logits. Was this intended?
  output, from_logits = _get_logits(


150/150 ━━━━━━━━━━━━━━━━━━━━ 41s 263ms/step - accuracy: 0.6365 - loss: 1.2672 - val_accuracy: 0.8914 - val_loss: 0.3902
Epoch 2/50
150/150 ━━━━━━━━━━━━━━━━━━━━ 39s 261ms/step - accuracy: 0.8984 - loss: 0.3694 - val_accuracy: 0.9228 - val_loss: 0.2696
Epoch 3/50
150/150 ━━━━━━━━━━━━━━━━━━━━ 39s 262ms/step - accuracy: 0.9260 - loss: 0.2626 - val_accuracy: 0.9420 - val_loss: 0.2051
Epoch 4/50
150/150 ━━━━━━━━━━━━━━━━━━━━ 40s 264ms/step - accuracy: 0.9403 - loss: 0.2111 - val_accuracy: 0.9488 - val_loss: 0.1787
Epoch 5/50
150/150 ━━━━━━━━━━━━━━━━━━━━ 39s 258ms/step - accuracy: 0.9454 - loss: 0.1828 - val_accuracy: 0.9542 - val_loss: 0.1526
Epoch 6/50
150/150 ━━━━━━━━━━━━━━━━━━━━ 39s 257ms/step - accuracy: 0.9541 - loss: 0.1586 - val_accuracy: 0.9594 - val_loss: 0.1361
Epoch 7/50
150/150 ━━━━━━━━━━━━━━━━━━━━ 39s 257ms/step - accuracy: 0.9591 - loss: 0.1417 - val_accuracy: 0.9646 - val_loss: 0.1264
Epoch 8/50
150/150 ━━━━━━━━━━━━━━━━━━━━ 39s 257ms/step - accuracy: 0.9638 - loss: 0.1292 - val

In [24]:
def plot_metrics(metric1, metric2):
    fig = go.Figure()
    x = np.arange(0,len(history.history[metric1]),1)
    y1 = history.history[metric1]
    y2 = history.history[metric2]
    # Add traces
    fig.add_trace(go.Scatter(x=x, y=y1,
                        mode='lines', marker = dict(size=6, color = '#D100FF'),
                        name=metric1))
    fig.add_trace(go.Scatter(x=x, y=y2,
                        mode='lines', marker = dict(size=6, color = '#1BFF00'),
                        name=metric2))
    fig.update_layout(title=metric1+' and '+metric2, width=800, height=400,
                      xaxis = dict(title = 'Epoch'))


    return fig

In [25]:
plot_metrics('accuracy','val_accuracy')

In [26]:
test_loss, test_acc = model1.evaluate(test_dataset, verbose=2)

35/35 - 3s - 74ms/step - accuracy: 0.9829 - loss: 0.0590


In [28]:
# Preprocess the test data
test_df = pd.read_csv('/kaggle/input/digit-recognizer/test.csv')
test_ar = np.empty((test_df.shape[0], 28, 28, 1))

for m in range(test_df.shape[0]):
    for i in range(28):
        for j in range(28):
            test_ar[m][i][j][0] = test_df.iloc[m, i * 28 + j]

test_ar = test_ar / 255.0  # Normalize the test data

In [29]:
# Predict using the trained model
predictions = model1.predict(test_ar)
predicted_labels = np.argmax(predictions, axis=1)

# Prepare the submission DataFrame
submission_df = pd.DataFrame({
    'ImageId': np.arange(1, len(predicted_labels) + 1),
    'Label': predicted_labels
})

# Save the submission file
submission_df.to_csv('/kaggle/working/cnn_results.csv', index=False)

875/875 ━━━━━━━━━━━━━━━━━━━━ 12s 14ms/step
